In [64]:
import pandas as pd
import altair as alt

# Look at the metadata

In [65]:
metadata_df = pd.read_json('../../data/covidtracking/states-metadata.json')

In [66]:
metadata_df.head()

state                                     covid19SiteOld  \
0    AK  http://dhss.alaska.gov/dph/Epi/id/Pages/COVID-...   
1    AL  http://www.alabamapublichealth.gov/infectiousd...   
2    AR  https://www.healthy.arkansas.gov/programs-serv...   
3    AS  http://www.samoagovt.ws/2020/03/ministry-of-he...   
4    AZ  https://www.azdhs.gov/preparedness/epidemiolog...   

                                         covid19Site  \
0  http://dhss.alaska.gov/dph/Epi/id/Pages/COVID-...   
1  https://alpublichealth.maps.arcgis.com/apps/op...   
2  https://www.healthy.arkansas.gov/programs-serv...   
3                 https://www.facebook.com/amsamgov/   
4  https://www.azdhs.gov/preparedness/epidemiolog...   

                                covid19SiteSecondary          twitter  \
0  http://dhss.alaska.gov/dph/Epi/id/Pages/COVID-...     @Alaska_DHSS   
1                                               None  @alpublichealth   
2                                               None          @adhpio   
3  https://www.americansamoa.gov/?fbclid=IwAR2EKT...             None   
4                                               None           @azdhs   

        pui    pum                                              notes  \
0  All data  False  Unclear if their reported number means "person...   
1   No data  False  Last negative count from 3/16. Last update tim...   
2  All data   True                                   Pending = "PUIs"   
3   No Data  False   American Samoa: No data, no confirmed cases yet.   
4  All data  False  Negative = “Ruled Out”. Negatives are from pub...   

             name  
0          Alaska  
1         Alabama  
2        Arkansas  
3  American Samoa  
4         Arizona

# Load most recent data and look at it

In [67]:
data_df = pd.read_json('../../data/covidtracking/states-daily.json')
data_df['date'] = pd.to_datetime(data_df['date'], format="%Y%m%d")

In [68]:
data_df.head()

date state  positive  negative  pending  death  total  \
0 2020-03-20    AK        12     686.0      NaN    NaN    698   
1 2020-03-20    AL        81      28.0      NaN    0.0    109   
2 2020-03-20    AR        96     351.0    203.0    NaN    650   
3 2020-03-20    AS         0       NaN      NaN    0.0      0   
4 2020-03-20    AZ        65     211.0    101.0    0.0    377   

            dateChecked  
0  2020-03-20T20:00:00Z  
1  2020-03-20T20:00:00Z  
2  2020-03-20T20:00:00Z  
3  2020-03-20T20:00:00Z  
4  2020-03-20T20:00:00Z

### Daily counts and totals

In [42]:
# compute daily differences
tdf = data_df.sort_values(['state', 'date'], ascending=[True, False]).set_index(['state', 'date'])
diffs_df = tdf[['positive', 'negative', 'death']].groupby(level='state').diff(periods=-1).dropna(how='all')
tdf_diff=tdf.join(diffs_df, rsuffix='_diff').reset_index()

# "Normalizing" the totals
tdf_diff['total_10'] = tdf_diff['total']/10.

In [43]:
# produce the charts for a few states

charts=[]
for state in ['WA', 'NY', 'NJ', 'MA', 'CA', 'LA', 'DC','TX','OK','FL','NC','GA']: 
    state_df = tdf_diff[tdf_diff['state'] == state].copy()

    state_df.loc[:,'daily_positive'] = state_df['positive'][::-1].diff()
    state_df.loc[:,'total_10'] = state_df['total']/10.

    base = alt.Chart(state_df, title=state).encode(alt.X('date', axis=alt.Axis(title='Date'))).properties(width=250, height=150)
    dailies = base.mark_bar(size=10).encode(alt.Y('daily_positive', axis=alt.Axis(title='Daily positive')))

    totals = base.mark_line(color='lightgreen').encode(alt.Y('total_10', axis=alt.Axis(title='Tests/10'))) 
    positives = totals.mark_line(color='red').encode(alt.Y('positive', axis=alt.Axis(title='# Positive')))
    cumulative = totals + positives

    charts.append(alt.layer(dailies, cumulative).resolve_scale(y='independent'))


alt.hconcat(*charts)

alt.HConcatChart(...)

### Counts per 100k

In [44]:
pop_df = pd.read_csv('../../data/geodata/us_pop_fung_2019.csv').set_index('ST')

In [45]:
most_recent_test_date = data_df['date'].max()
most_recent_df = data_df[data_df['date'] == most_recent_test_date].set_index('state')
print("Most recent test date", most_recent_test_date)
print(len(most_recent_df), "states/territories have data on this date.")

Most recent test date 2020-03-20 00:00:00
56 states/territories have data on this date.


In [46]:
#create a couple of columns for testing rate analysis
most_recent_df['total/100k'] = (most_recent_df['total'] / pop_df['Population']) * 100000
most_recent_df['total/positive'] = (most_recent_df['total'] / most_recent_df['positive'])
most_recent_df = most_recent_df.reset_index()

In [47]:
most_recent_df.head()

state       date  positive  negative  pending  death  total  \
0    AK 2020-03-20        12     686.0      NaN    NaN    698   
1    AL 2020-03-20        81      28.0      NaN    0.0    109   
2    AR 2020-03-20        96     351.0    203.0    NaN    650   
3    AS 2020-03-20         0       NaN      NaN    0.0      0   
4    AZ 2020-03-20        65     211.0    101.0    0.0    377   

            dateChecked  total/100k  total/positive  
0  2020-03-20T20:00:00Z   95.414499       58.166667  
1  2020-03-20T20:00:00Z    2.223045        1.345679  
2  2020-03-20T20:00:00Z   21.538691        6.770833  
3  2020-03-20T20:00:00Z         NaN             NaN  
4  2020-03-20T20:00:00Z    5.179484        5.800000

In [31]:
chart = alt.Chart(most_recent_df.sort_values('total/100k'), title="Tests per 100k")
chart.mark_bar().encode(alt.X('state', sort='y'), alt.Y('total/100k'))

alt.Chart(...)

# Tests per 100k Population & Total Positives

In [32]:
#Load most recent data and city population counts
data_df = pd.read_json('../../data/covidtracking/states-daily.json')
data_df['date'] = pd.to_datetime(data_df['date'], format="%Y%m%d")
pop_df = pd.read_csv('../../data/geodata/us_pop_fung_2019.csv').set_index('ST')

In [33]:
most_recent_test_date = data_df['date'].max()
most_recent_df = data_df[data_df['date'] == most_recent_test_date].set_index('state')
print("Most recent test date", most_recent_test_date)
print(len(most_recent_df), "states/territories have data on this date.")

Most recent test date 2020-03-20 00:00:00
56 states/territories have data on this date.


In [34]:
most_recent_df['tests/100k'] = round((most_recent_df['total'] / pop_df['Population']) * 100000,2)
most_recent_df['pos/100k'] = round((most_recent_df['positive'] / pop_df['Population']) * 100000,2)
most_recent_df['total/positive'] = round((most_recent_df['total'] / most_recent_df['positive']),2)
most_recent_df = most_recent_df.reset_index()

In [35]:
most_recent_df.head()

state       date  positive  negative  pending  death  total  \
0    AK 2020-03-20        12     686.0      NaN    NaN    698   
1    AL 2020-03-20        81      28.0      NaN    0.0    109   
2    AR 2020-03-20        96     351.0    203.0    NaN    650   
3    AS 2020-03-20         0       NaN      NaN    0.0      0   
4    AZ 2020-03-20        65     211.0    101.0    0.0    377   

            dateChecked  tests/100k  pos/100k  total/positive  
0  2020-03-20T20:00:00Z       95.41      1.64           58.17  
1  2020-03-20T20:00:00Z        2.22      1.65            1.35  
2  2020-03-20T20:00:00Z       21.54      3.18            6.77  
3  2020-03-20T20:00:00Z         NaN       NaN             NaN  
4  2020-03-20T20:00:00Z        5.18      0.89            5.80

In [36]:
#resort dataframe in ascending order of testing rates per 100k population
source_df = most_recent_df.sort_values('tests/100k')

#drop data points without total testing info
source_df =source_df.dropna(subset=['tests/100k'])

#now create some layers for the chart
base = alt.Chart(source_df,
                 title='COVID-19 in the States : tests and positive cases / 100k Population').encode(
                    alt.X('state',sort='x'))
    
bar = base.mark_bar(color='lightgrey').encode(
    alt.X('state',sort='x'),
    alt.Y('tests/100k',axis=alt.Axis(title='Tests / 100k population',grid=True)),
    tooltip=['state','pos/100k','tests/100k','positive']
)

#positive cases as absolute number
circle = base.mark_circle(color='blue',size=60).encode(
    alt.X('state',sort='x'),
    alt.Y('positive', axis=alt.Axis(title='Positive COVID-19 Cases')),
    tooltip=['state','positive','tests/100k']
)

#postives per 100,000 pop
circle2 = base.mark_circle(color='blue',size=60).encode(
    alt.X('state',sort='x'),
    alt.Y('pos/100k', axis=alt.Axis(title='Positive COVID-19 Cases/100k population',tickMinStep=5)),
    tooltip=['state','pos/100k','tests/100k','positive']
)

#assemble the chart with two independent y-axes
bigChart = alt.layer(bar,circle2).resolve_scale(y='independent').properties(width=800,height=600)
bigChart

alt.LayerChart(...)

In [41]:
source_df.tail(20)


state       date  positive  negative  pending  death  total  \
8     DC 2020-03-19        39     153.0     11.0    0.0    203   
53    WI 2020-03-19       155    2192.0      NaN    NaN   2347   
6     CO 2020-03-19       216    2112.0      NaN    2.0   2328   
40    OR 2020-03-19        88    1329.0    437.0    3.0   1854   
21    MA 2020-03-19       328    2804.0      NaN    NaN   3132   
55    WY 2020-03-19        18     271.0      NaN    NaN    289   
48    UT 2020-03-19        78    1526.0      NaN    0.0   1604   
25    MN 2020-03-19        89    2949.0      NaN    NaN   3038   
0     AK 2020-03-19         6     400.0      NaN    NaN    406   
36    NV 2020-03-19        95    1626.0      NaN    1.0   1721   
33    NH 2020-03-19        39     621.0    231.0    NaN    891   
31    ND 2020-03-19        15     493.0      NaN    0.0    508   
29    MT 2020-03-19        12     761.0      0.0    NaN    773   
43    RI 2020-03-19        33     540.0    334.0    NaN    907   
51    VT 2020-03-19        22     645.0      NaN    NaN    667   
45    SD 2020-03-19        11     551.0    385.0    1.0    947   
37    NY 2020-03-19      4152   18132.0      NaN   12.0  22284   
35    NM 2020-03-19        35    2762.0      NaN    NaN   2797   
23    ME 2020-03-19        53    2004.0      NaN    NaN   2057   
52    WA 2020-03-19      1187   15918.0      NaN   66.0  17105   

             dateChecked  tests/100k  
8   2020-03-19T20:00:00Z       28.76  
53  2020-03-19T20:00:00Z       40.31  
6   2020-03-19T20:00:00Z       40.43  
40  2020-03-19T20:00:00Z       43.96  
21  2020-03-19T20:00:00Z       45.07  
55  2020-03-19T20:00:00Z       49.93  
48  2020-03-19T20:00:00Z       50.03  
25  2020-03-19T20:00:00Z       53.87  
0   2020-03-19T20:00:00Z       55.50  
36  2020-03-19T20:00:00Z       55.87  
33  2020-03-19T20:00:00Z       65.53  
31  2020-03-19T20:00:00Z       66.66  
29  2020-03-19T20:00:00Z       72.33  
43  2020-03-19T20:00:00Z       85.62  
51  2020-03-19T20:00:00Z      106.89  
45  2020-03-19T20:00:00Z      107.05  
37  2020-03-19T20:00:00Z      114.55  
35  2020-03-19T20:00:00Z      133.39  
23  2020-03-19T20:00:00Z      153.03  
52  2020-03-19T20:00:00Z      224.63

In [47]:
#  Cases per 100,000 population

In [43]:
#Load most recent data and city population counts
data_df = pd.read_json('../../data/covidtracking/states-daily.json')
data_df['date'] = pd.to_datetime(data_df['date'], format="%Y%m%d")
pop_df = pd.read_csv('../../data/geodata/us_pop_fung_2019.csv').set_index('ST')


In [44]:
most_recent_test_date = data_df['date'].max()
most_recent_df = data_df[data_df['date'] == most_recent_test_date].set_index('state')
print("Most recent test date", most_recent_test_date)
print(len(most_recent_df), "states/territories have data on this date.")

Most recent test date 2020-03-19 00:00:00
56 states/territories have data on this date.


In [45]:
#add state populations to dataframe
most_recent_df['population'] = pop_df['Population']
most_recent_df = most_recent_df.reset_index()

In [46]:
popChart = alt.Chart(most_recent_df, title='Postive Cases vs. Population by US State').mark_circle(size=80).encode(
    alt.X('population',axis=alt.Axis(title='State Population')),
    alt.Y('positive', axis=alt.Axis(title='COVID-19 Positive Individuals')),
    tooltip=['state','population','positive','total']
).properties(width=800, height=600)

popChart = popChart + popChart.transform_regression('population','positive').mark_line()

popChart.interactive()

alt.LayerChart(...)

In [ ]:
#Cases by State in Order of Number

In [79]:
chart = alt.Chart(most_recent_df.sort_values('total/positive'), title="Tests per Positve Case")
chart.mark_bar().encode(alt.X('state', sort='y'), alt.Y('total/positive')).properties (width=800,height=600)

alt.Chart(...)